# MNIST свёрточными сетями

## Читаем данные

In [9]:
tf.__version__
import keras
keras.__version__


AttributeError: module 'tensorflow' has no attribute '__version__'

In [1]:
import numpy as np,tensorflow as tf

import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_style("whitegrid")
sns.set_palette("colorblind")
palette = sns.color_palette()
figsize = (10,10)
legend_fontsize = 16

In [2]:
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)

Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Instructions for updating:
Please use tf.one_hot on tensors.
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.


## Свёртки на TensorFlow

In [3]:
x = tf.placeholder(tf.float32, [None, 784]) 
y = tf.placeholder(tf.float32, [None, 10])
keep_probability = tf.placeholder(tf.float32)

x_image = tf.reshape(x, [-1,28,28,1])

W_conv_0 = tf.Variable(tf.truncated_normal([5, 5, 1, 32], stddev=0.1))
b_conv_0 = tf.Variable(tf.constant(0.1, shape=[32]))

conv_0 = tf.nn.conv2d(x_image, W_conv_0, strides=[1, 1, 1, 1], padding='SAME') + b_conv_0
# [-1,28,28,32]

h_conv_0 = tf.nn.relu(conv_0)
h_pool_0 = tf.nn.max_pool(h_conv_0, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')
# [-1,14,14,32]

h_pool_1_flat = tf.reshape(h_pool_0, [-1, 14*14*32])

W_fc_1 = tf.Variable(tf.truncated_normal([14*14*32, 10], stddev=0.1))
b_fc_1 = tf.Variable(tf.constant(0.1, shape=[10]))

logit_conv = tf.matmul(h_pool_1_flat, W_fc_1) + b_fc_1
y_conv = tf.nn.softmax(logit_conv)

In [4]:
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

l2 = tf.contrib.layers.l2_regularizer(0.1)
cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(logits=logit_conv, labels=y)) + \
                    l2(W_conv_0) #+ l2(W_conv_1)# + l1(W_conv_0) + l1(W_conv_1) + l1(W_conv_2)

train_step = tf.train.AdamOptimizer(0.0001).minimize(cross_entropy)

Instructions for updating:

Future major versions of TensorFlow will allow gradients to flow
into the labels input on backprop by default.

See `tf.nn.softmax_cross_entropy_with_logits_v2`.



In [5]:
sess = tf.Session(config=tf.ConfigProto(log_device_placement=True))
sess.run(tf.initialize_all_variables())
batch_xs, batch_ys = mnist.train.next_batch(64)
sess.run(train_step, feed_dict={x: batch_xs, y: batch_ys, keep_probability: 0.5})

Instructions for updating:
Use `tf.global_variables_initializer` instead.


In [6]:
for i in range(20001):
    batch_xs, batch_ys = mnist.train.next_batch(64)
    sess.run(train_step, feed_dict={x: batch_xs, y: batch_ys, keep_probability: 0.5})
#     break
    if i % 50 == 0:
        test_xs, test_ys = mnist.test.next_batch(128)
        acc = sess.run(accuracy, feed_dict={x: test_xs, y: test_ys, keep_probability: 1.})
        print("Точность %s: %s" % (i, acc))
    if i > 0 and i % 1000 == 0:
        print("[%d]\ttrain accuracy=%.6f\ttest accuracy=%.6f" % (i,
            sess.run(accuracy, feed_dict={x: mnist.train.images, y: mnist.train.labels}),
            sess.run(accuracy, feed_dict={x: mnist.test.images, y: mnist.test.labels})
        ))

Точность 0: 0.046875
Точность 50: 0.2734375
Точность 100: 0.4921875
Точность 150: 0.6484375
Точность 200: 0.7109375
Точность 250: 0.7578125
Точность 300: 0.8125
Точность 350: 0.8984375
Точность 400: 0.90625
Точность 450: 0.8515625
Точность 500: 0.8828125
Точность 550: 0.9296875
Точность 600: 0.84375
Точность 650: 0.8515625
Точность 700: 0.8984375
Точность 750: 0.8984375
Точность 800: 0.90625
Точность 850: 0.890625
Точность 900: 0.875
Точность 950: 0.875
Точность 1000: 0.90625
[1000]	train accuracy=0.893182	test accuracy=0.900700
Точность 1050: 0.875
Точность 1100: 0.9375
Точность 1150: 0.9453125
Точность 1200: 0.875
Точность 1250: 0.90625
Точность 1300: 0.859375
Точность 1350: 0.9296875
Точность 1400: 0.96875
Точность 1450: 0.921875
Точность 1500: 0.9296875
Точность 1550: 0.9453125
Точность 1600: 0.890625
Точность 1650: 0.9140625
Точность 1700: 0.890625
Точность 1750: 0.8671875
Точность 1800: 0.9140625
Точность 1850: 0.8828125
Точность 1900: 0.96875
Точность 1950: 0.9375
Точность 2000:

Точность 15150: 0.96875
Точность 15200: 0.96875
Точность 15250: 0.9921875
Точность 15300: 0.9765625
Точность 15350: 0.984375
Точность 15400: 0.96875
Точность 15450: 0.9453125
Точность 15500: 0.96875
Точность 15550: 0.96875
Точность 15600: 0.953125
Точность 15650: 0.9453125
Точность 15700: 0.96875
Точность 15750: 0.96875
Точность 15800: 0.9765625
Точность 15850: 0.9609375
Точность 15900: 0.96875
Точность 15950: 0.9609375
Точность 16000: 0.9609375
[16000]	train accuracy=0.968236	test accuracy=0.970300
Точность 16050: 0.9765625
Точность 16100: 0.984375
Точность 16150: 0.984375
Точность 16200: 0.9921875
Точность 16250: 0.96875
Точность 16300: 0.9375
Точность 16350: 0.96875
Точность 16400: 0.9609375
Точность 16450: 0.953125
Точность 16500: 0.953125
Точность 16550: 0.9453125
Точность 16600: 0.9609375
Точность 16650: 0.9765625
Точность 16700: 0.953125
Точность 16750: 0.984375
Точность 16800: 0.9765625
Точность 16850: 0.9765625
Точность 16900: 0.984375
Точность 16950: 0.984375
Точность 17000: 

## Двухуровневая свёрточная сеть

In [7]:
x = tf.placeholder(tf.float32, [None, 784]) 
y = tf.placeholder(tf.float32, [None, 10])
keep_probability = tf.placeholder(tf.float32)

x_image = tf.reshape(x, [-1,28,28,1])

W_conv_0 = tf.Variable(tf.truncated_normal([5, 5, 1, 32], stddev=0.1))
b_conv_0 = tf.Variable(tf.constant(0.1, shape=[32]))

conv_0 = tf.nn.conv2d(x_image, W_conv_0, strides=[1, 1, 1, 1], padding='SAME') + b_conv_0

h_conv_0 = tf.nn.relu(conv_0)
h_pool_0 = tf.nn.max_pool(h_conv_0, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')

W_conv_1 = tf.Variable(tf.truncated_normal([5, 5, 32, 64], stddev=0.1))
b_conv_1 = tf.Variable(tf.constant(0.1, shape=[64]))

conv_1 = tf.nn.conv2d(h_pool_0, W_conv_1, strides=[1, 1, 1, 1], padding='SAME') + b_conv_1

h_conv_1 = tf.nn.relu(conv_1)
h_pool_1 = tf.nn.max_pool(h_conv_1, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')
h_pool_1_flat = tf.reshape(h_pool_1, [-1, 7*7*64])

W_fc_2 = tf.Variable(tf.truncated_normal([7*7*64, 10], stddev=0.1))
b_fc_2 = tf.Variable(tf.constant(0.1, shape=[10]))

logit_conv = tf.matmul(h_pool_1_flat, W_fc_2) + b_fc_2
y_conv = tf.nn.softmax(logit_conv)

In [8]:
correct_prediction = tf.equal(tf.argmax(y_conv, 1), tf.argmax(y, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, tf.float32))

l2 = tf.contrib.layers.l2_regularizer(0.1)
cross_entropy = tf.reduce_mean(tf.nn.softmax_cross_entropy_with_logits(logit_conv, y))
#+ \
 #                   l2(W_conv_0) #+ l2(W_conv_1)# + l1(W_conv_0) + l1(W_conv_1) + l1(W_conv_2)

train_step = tf.train.AdamOptimizer().minimize(cross_entropy)

ValueError: Only call `softmax_cross_entropy_with_logits` with named arguments (labels=..., logits=..., ...)

In [ ]:
sess = tf.Session()
sess.run(tf.initialize_all_variables())

In [ ]:
for i in range(20001):
    batch_xs, batch_ys = mnist.train.next_batch(64)
    sess.run(train_step, feed_dict={x: batch_xs, y: batch_ys, keep_probability: 0.5})
    if i % 50 == 0:
        test_xs, test_ys = mnist.test.next_batch(128)
        acc = sess.run(accuracy, feed_dict={x: test_xs, y: test_ys, keep_probability: 1.})
        print("Точность %s: %s" % (i, acc))
    if i > 0 and i % 1000 == 0:
        print("[%d]\ttest accuracy=%.6f" % (i,
#             sess.run(accuracy, feed_dict={x: mnist.train.images, y: mnist.train.labels}),
            sess.run(accuracy, feed_dict={x: mnist.test.images, y: mnist.test.labels})
        ))